## **DAA - Dados e Aprendizagem Automática**
### MCI to AD Progression Prediction Using Brain MRI Analysis
#### Group 2

In [120]:
import sklearn as skl
import pandas as pd
pd.set_option('display.max_info_columns', 3000)
pd.set_option('display.max_columns', 3000)
pd.set_option('display.max_rows', 3000)
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV, StratifiedShuffleSplit
from sklearn import tree

from sklearn.feature_selection import chi2
from sklearn.preprocessing import StandardScaler,LabelEncoder, MinMaxScaler

from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier, VotingClassifier, BaggingClassifier, StackingClassifier
from sklearn.linear_model import LogisticRegression
import xgboost as xgb
from xgboost.sklearn import XGBClassifier

from sklearn.metrics import classification_report
%matplotlib inline

from main import preprocess

### **Data Analysis / Preparation**

**Import dataset**

In [98]:
df = pd.read_csv('datasets/train_radiomics_hipocamp.csv')

In [99]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 305 entries, 0 to 304
Data columns (total 2181 columns):
 #     Column                                                         Non-Null Count  Dtype  
---    ------                                                         --------------  -----  
 0     ID                                                             305 non-null    object 
 1     Image                                                          305 non-null    object 
 2     Mask                                                           305 non-null    object 
 3     diagnostics_Versions_PyRadiomics                               305 non-null    object 
 4     diagnostics_Versions_Numpy                                     305 non-null    object 
 5     diagnostics_Versions_SimpleITK                                 305 non-null    object 
 6     diagnostics_Versions_PyWavelet                                 305 non-null    object 
 7     diagnostics_Versions_Python             

In [100]:
df.head()

ID                                              Image  \
0  006_S_0681  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  941_S_1203  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  011_S_0003  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  057_S_0779  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  033_S_0920  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

                                                Mask  \
0  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

  diagnostics_Versions_PyRadiomics diagnostics_Versions_Numpy  \
0                            2.2.0                     1.18.5   
1                            2.2.0                     1.18.5   
2                            2.2.0                     1.18.5   
3                            2.2.0                     1.18.5   
4                            2.2.0                     1.18.5   

  diagnostics_Versions_SimpleITK diagnostics_Versions_PyWavelet  \
0                          1.2.4                          1.1.1   
1                          1.2.4                          1.1.1   
2                          1.2.4                          1.1.1   
3                          1.2.4                          1.1.1   
4                          1.2.4                          1.1.1   

  diagnostics_Versions_Python  \
0                       3.7.7   
1                       3.7.7   
2                       3.7.7   
3                       3.7.7   
4                       3.7.7   

                  diagnostics_Configuration_Settings  \
0  {'minimumROIDimensions': 2, 'minimumROISize': ...   
1  {'minimumROIDimensions': 2, 'minimumROISize': ...   
2  {'minimumROIDimensions': 2, 'minimumROISize': ...   
3  {'minimumROIDimensions': 2, 'minimumROISize': ...   
4  {'minimumROIDimensions': 2, 'minimumROISize': ...   

         diagnostics_Configuration_EnabledImageTypes  \
0  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
1  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
2  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
3  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   
4  {'Original': {}, 'Wavelet': {}, 'LoG': {'sigma...   

            diagnostics_Image-original_Hash  \
0  b5d774a32163a7ee822d42a07808a787f8687f56   
1  397042d736bd790b7880b372b1749ff424f89cbe   
2  84d679a88812c4aaf03a6d99f00c913b2f64506f   
3  168f330d2ca3f097146e5d041f33b40672d230df   
4  ea5f291ea107dfda5e5c725eae7c0555ced44ce4   

   diagnostics_Image-original_Dimensionality  \
0                                          3   
1                                          3   
2                                          3   
3                                          3   
4                                          3   

  diagnostics_Image-original_Spacing diagnostics_Image-original_Size  \
0                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
1                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
2                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
3                    (1.0, 1.0, 1.0)                 (256, 256, 256)   
4                    (1.0, 1.0, 1.0)                 (256, 256, 256)   

   diagnostics_Image-original_Mean  diagnostics_Image-original_Minimum  \
0                         5.848123                                   0   
1                         5.238834                                   0   
2                         6.816667                                   0   
3                         6.445162                                   0   
4                         5.568269                                   0   

   diagnostics_Image-original_Maximum  \
0                                 178   
1                                 190   
2                        

**Missing values?**

In [101]:
print("Total:", df.isna().sum().sum())

Total: 0


**Repeated values?**

In [102]:
# drop duplicate rows
prev = len(df)
df.drop_duplicates(inplace=True)
print("Total rows:", len(df))

Total rows: 305


**Columns with always-repeated values?**

In [103]:
unique_dict = df.nunique().to_dict()
no_unique_values = {col: count for col, count in unique_dict.items() if count == 1}
print("Total:",df.nunique().tolist().count(1))

Total: 159


**Drop columns with always-repeated values**

In [104]:
drop = [col for col, _ in no_unique_values.items()]
df.drop(drop, axis=1, inplace=True)
df.head()

ID                                              Image  \
0  006_S_0681  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  941_S_1203  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  011_S_0003  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  057_S_0779  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  033_S_0920  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

                                                Mask  \
0  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

            diagnostics_Image-original_Hash  diagnostics_Image-original_Mean  \
0  b5d774a32163a7ee822d42a07808a787f8687f56                         5.848123   
1  397042d736bd790b7880b372b1749ff424f89cbe                         5.238834   
2  84d679a88812c4aaf03a6d99f00c913b2f64506f                         6.816667   
3  168f330d2ca3f097146e5d041f33b40672d230df                         6.445162   
4  ea5f291ea107dfda5e5c725eae7c0555ced44ce4                         5.568269   

   diagnostics_Image-original_Maximum  \
0                                 178   
1                                 190   
2                                 155   
3                                 171   
4                                 150   

             diagnostics_Mask-original_Hash  \
0  315bdd7a06bb73df17bfc1297398b4398e36e180   
1  208a2b034b72592489315104ef526ca10d434f24   
2  352220437f6381b051fd4173969519887b530df6   
3  9f62584e8badeb5de90b797d0c86c5170465d90f   
4  62ab23b0a4ea4c9e7574b1ea410bd90236fe1d6e   

  diagnostics_Mask-original_BoundingBox  diagnostics_Mask-original_VoxelNum  \
0            (103, 113, 93, 36, 30, 71)                                7106   
1             (81, 127, 93, 47, 16, 73)                                7779   
2             (77, 119, 89, 49, 30, 81)                                6707   
3             (93, 102, 90, 41, 29, 78)                                8281   
4             (87, 119, 91, 40, 27, 75)                                5986   

         diagnostics_Mask-original_CenterOfMassIndex  \
0  (121.94230227976358, 129.27272727272728, 128.4...   
1  (107.06170458927883, 135.28088443244633, 128.2...   
2  (103.3640972118682, 135.28164604144922, 128.98...   
3  (116.29827315541601, 118.67431469629271, 129.3...   
4  (108.26561977948546, 132.05462746408287, 127.6...   

              diagnostics_Mask-original_CenterOfMass  \
0  (121.94230227976358, 129.27272727272728, 128.4...   
1  (107.06170458927883, 135.28088443244633, 128.2...   
2  (103.3640972118682, 135.28164604144922, 128.98...   
3  (116.29827315541601, 118.67431469629271, 129.3...   
4  (108.26561977948546, 132.05462746408287, 127.6...   

   original_shape_Elongation  original_shape_Flatness  \
0                   0.420040                 0.106547   
1                   0.425482                 0.102532   
2                   0.447685                 0.135582   
3                   0.418896                 0.099626   
4                   0.411851                 0.080719   

   original_shape_LeastAxisLength  original_shape_MajorAxisLength  \
0                       10.757474                      100.964915   
1                       10.432362                      101.747321   
2                       14.370911                      105.993915   
3                       10.639815                      106.797600   
4                        8.885188                      110.075144   

   original_shape_Maximum2DDiameterColumn  \
0                               72.034714   
1                               73.246160   
2                               79.762146   
3                               78.102497   
4                               75.432089   

   original_shape_Maximum2DDiameterRow  original_shape_Maximum2DDiameterSlic

**Categorical features**

In [105]:
for col in [col for col in df.columns if df[col].dtype == 'object']:
    print(col)

ID
Image
Mask
diagnostics_Image-original_Hash
diagnostics_Mask-original_Hash
diagnostics_Mask-original_BoundingBox
diagnostics_Mask-original_CenterOfMassIndex
diagnostics_Mask-original_CenterOfMass
Transition


**Categorical features with all-unique values?**

In [106]:
all_unique = [col for col, count in unique_dict.items() if count == df.shape[0] and df[col].dtype == 'object']
for col in all_unique:
    print(col)

ID
Image
Mask
diagnostics_Image-original_Hash
diagnostics_Mask-original_Hash
diagnostics_Mask-original_BoundingBox
diagnostics_Mask-original_CenterOfMassIndex
diagnostics_Mask-original_CenterOfMass


In [107]:
df.filter(items=all_unique).head()

ID                                              Image  \
0  006_S_0681  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  941_S_1203  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  011_S_0003  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  057_S_0779  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  033_S_0920  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

                                                Mask  \
0  /notebooks/disk2/DS2_FreeSurfer/ADNI_006_S_068...   
1  /notebooks/disk2/DS2_FreeSurfer/ADNI_941_S_120...   
2  /notebooks/disk2/DS2_FreeSurfer/ADNI_011_S_000...   
3  /notebooks/disk2/DS2_FreeSurfer/ADNI_057_S_077...   
4  /notebooks/disk2/DS2_FreeSurfer/ADNI_033_S_092...   

            diagnostics_Image-original_Hash  \
0  b5d774a32163a7ee822d42a07808a787f8687f56   
1  397042d736bd790b7880b372b1749ff424f89cbe   
2  84d679a88812c4aaf03a6d99f00c913b2f64506f   
3  168f330d2ca3f097146e5d041f33b40672d230df   
4  ea5f291ea107dfda5e5c725eae7c0555ced44ce4   

             diagnostics_Mask-original_Hash  \
0  315bdd7a06bb73df17bfc1297398b4398e36e180   
1  208a2b034b72592489315104ef526ca10d434f24   
2  352220437f6381b051fd4173969519887b530df6   
3  9f62584e8badeb5de90b797d0c86c5170465d90f   
4  62ab23b0a4ea4c9e7574b1ea410bd90236fe1d6e   

  diagnostics_Mask-original_BoundingBox  \
0            (103, 113, 93, 36, 30, 71)   
1             (81, 127, 93, 47, 16, 73)   
2             (77, 119, 89, 49, 30, 81)   
3             (93, 102, 90, 41, 29, 78)   
4             (87, 119, 91, 40, 27, 75)   

         diagnostics_Mask-original_CenterOfMassIndex  \
0  (121.94230227976358, 129.27272727272728, 128.4...   
1  (107.06170458927883, 135.28088443244633, 128.2...   
2  (103.3640972118682, 135.28164604144922, 128.98...   
3  (116.29827315541601, 118.67431469629271, 129.3...   
4  (108.26561977948546, 132.05462746408287, 127.6...   

              diagnostics_Mask-original_CenterOfMass  
0  (121.94230227976358, 129.27272727272728, 128.4...  
1  (107.06170458927883, 135.28088443244633, 128.2...  
2  (103.3640972118682, 135.28164604144922, 128.98...  
3  (116.29827315541601, 118.67431469629271, 129.3...  
4  (108.26561977948546, 132.05462746408287, 127.6...

The features `diagnostics_Mask-original_BoundingBox`, `diagnostics_Mask-original_CenterOfMassIndex` and `diagnostics_Mask-original_CenterOfMass` contain valuable information about the size, location and center of mass of the hippocampus, in the form of coordinates, and therefore could be useful for our model.

The remaining features have all-unique string values representing image paths and hashes, and therefore aren't useful for our model.

**Drop unuseful all-unique categorical columns**

In [108]:
df.drop(list(set(all_unique) - set(['diagnostics_Mask-original_BoundingBox', 'diagnostics_Mask-original_CenterOfMassIndex', 'diagnostics_Mask-original_CenterOfMass'])), axis=1, inplace=True)
df.head()

diagnostics_Image-original_Mean  diagnostics_Image-original_Maximum  \
0                         5.848123                                 178   
1                         5.238834                                 190   
2                         6.816667                                 155   
3                         6.445162                                 171   
4                         5.568269                                 150   

  diagnostics_Mask-original_BoundingBox  diagnostics_Mask-original_VoxelNum  \
0            (103, 113, 93, 36, 30, 71)                                7106   
1             (81, 127, 93, 47, 16, 73)                                7779   
2             (77, 119, 89, 49, 30, 81)                                6707   
3             (93, 102, 90, 41, 29, 78)                                8281   
4             (87, 119, 91, 40, 27, 75)                                5986   

         diagnostics_Mask-original_CenterOfMassIndex  \
0  (121.94230227976358, 129.27272727272728, 128.4...   
1  (107.06170458927883, 135.28088443244633, 128.2...   
2  (103.3640972118682, 135.28164604144922, 128.98...   
3  (116.29827315541601, 118.67431469629271, 129.3...   
4  (108.26561977948546, 132.05462746408287, 127.6...   

              diagnostics_Mask-original_CenterOfMass  \
0  (121.94230227976358, 129.27272727272728, 128.4...   
1  (107.06170458927883, 135.28088443244633, 128.2...   
2  (103.3640972118682, 135.28164604144922, 128.98...   
3  (116.29827315541601, 118.67431469629271, 129.3...   
4  (108.26561977948546, 132.05462746408287, 127.6...   

   original_shape_Elongation  original_shape_Flatness  \
0                   0.420040                 0.106547   
1                   0.425482                 0.102532   
2                   0.447685                 0.135582   
3                   0.418896                 0.099626   
4                   0.411851                 0.080719   

   original_shape_LeastAxisLength  original_shape_MajorAxisLength  \
0                       10.757474                      100.964915   
1                       10.432362                      101.747321   
2                       14.370911                      105.993915   
3                       10.639815                      106.797600   
4                        8.885188                      110.075144   

   original_shape_Maximum2DDiameterColumn  \
0                               72.034714   
1                               73.246160   
2                               79.762146   
3                               78.102497   
4                               75.432089   

   original_shape_Maximum2DDiameterRow  original_shape_Maximum2DDiameterSlice  \
0                            71.175839                              43.416587   
1                            73.109507                              44.102154   
2                            79.056942                              47.853944   
3                            77.006493                              45.793013   
4                            75.239617                              43.462628   

   original_shape_Maximum3DDiameter  original_shape_MeshVolume  \
0                         72.034714                7033.166667   
1                         73.252986                7716.583333   
2                         81.154174                6636.083333   
3                         78.217645                8248.583333   
4                         75.848533                5897.791667   

   original_shape_MinorAxisLength  original_shape_Sphericity  \
0                       42.409319                   0.396075   
1                       43.291655                   0.420557   
2                       47.451935                   0.315524   
3                       44.737083                   0.401709   
4                       45.334518                   0.390626   

   original_shape_SurfaceArea  original_shape_SurfaceVolumeRatio  \
0                 4482.023762              

**Handle remaining categorical features**

Since `diagnostics_Mask-original_BoundingBox` contains the bounding box coordinates of the region of interest, in this case the hippocampus, we can calculate the volume of this region to make the data more useful to our model, since a shrinkage of the hippocampus is linked to MCI (as stated in this project's assignment paper).

In [109]:
for value in df['diagnostics_Mask-original_BoundingBox']:
    coordinates = value.split(', ')
    x_max, y_max, z_max, x_min, y_min, z_min = [int(coordinate.replace("(", "").replace(")", "")) for coordinate in coordinates]
    if x_max <= x_min or y_max <= y_min or z_max <= z_min:
        print(coordinates)

['(94', '142', '86', '49', '20', '86)']
['(95', '118', '85', '42', '15', '89)']


Bounding box coordinates are usually structured as such: `(x_min, y_min, z_min, x_max, y_max, z_max)`. However, by analyzing the data we can observe that the first 3 values are always bigger than the last 3 (except in two ocasions), so we can assume this data is actually being given to us as:  `(x_max, y_max, z_max, x_min, y_min, z_min)`.

In [110]:
volumes = []
i = 0

for value in df['diagnostics_Mask-original_BoundingBox']:
    coordinates = value.split(', ')
    x_max, y_max, z_max, x_min, y_min, z_min = [
        int(coordinate.replace("(", "").replace(")", "")) for coordinate in coordinates]
    # drop rows with invalid bounding box coordinates (max <= min)
    if x_max <= x_min or y_max <= y_min or z_max <= z_min:
        df.drop(i, axis=0, inplace=True)
    else:
        volumes.append((x_max - x_min) * (y_max - y_min) * (z_max - z_min))
    i += 1

df.drop(['diagnostics_Mask-original_BoundingBox'], axis=1, inplace=True)
df['BoundingBox_Volume'] = volumes
df['BoundingBox_Volume'].describe()

count       303.000000
mean      79651.904290
std       35929.173749
min        4717.000000
25%       53241.500000
50%       77658.000000
75%      107082.500000
max      187404.000000
Name: BoundingBox_Volume, dtype: float64

In [111]:
com_x = []
com_y = []
com_z = []

for value in df['diagnostics_Mask-original_CenterOfMassIndex']:
    coordinates = value.split(', ')
    x, y, z = [float(coordinate.replace("(", "").replace(")", "")) for coordinate in coordinates]
    com_x.append(x)
    com_y.append(y)
    com_z.append(z)

df.drop(['diagnostics_Mask-original_CenterOfMassIndex'], axis=1, inplace=True)
df.drop(['diagnostics_Mask-original_CenterOfMass'], axis=1, inplace=True)
df['CenterOfMass_X'] = com_x
df['CenterOfMass_Y'] = com_y
df['CenterOfMass_Z'] = com_z

df.head()

diagnostics_Image-original_Mean  diagnostics_Image-original_Maximum  \
0                         5.848123                                 178   
1                         5.238834                                 190   
2                         6.816667                                 155   
3                         6.445162                                 171   
4                         5.568269                                 150   

   diagnostics_Mask-original_VoxelNum  original_shape_Elongation  \
0                                7106                   0.420040   
1                                7779                   0.425482   
2                                6707                   0.447685   
3                                8281                   0.418896   
4                                5986                   0.411851   

   original_shape_Flatness  original_shape_LeastAxisLength  \
0                 0.106547                       10.757474   
1                 0.102532                       10.432362   
2                 0.135582                       14.370911   
3                 0.099626                       10.639815   
4                 0.080719                        8.885188   

   original_shape_MajorAxisLength  original_shape_Maximum2DDiameterColumn  \
0                      100.964915                               72.034714   
1                      101.747321                               73.246160   
2                      105.993915                               79.762146   
3                      106.797600                               78.102497   
4                      110.075144                               75.432089   

   original_shape_Maximum2DDiameterRow  original_shape_Maximum2DDiameterSlice  \
0                            71.175839                              43.416587   
1                            73.109507                              44.102154   
2                            79.056942                              47.853944   
3                            77.006493                              45.793013   
4                            75.239617                              43.462628   

   original_shape_Maximum3DDiameter  original_shape_MeshVolume  \
0                         72.034714                7033.166667   
1                         73.252986                7716.583333   
2                         81.154174                6636.083333   
3                         78.217645                8248.583333   
4                         75.848533                5897.791667   

   original_shape_MinorAxisLength  original_shape_Sphericity  \
0                       42.409319                   0.396075   
1                       43.291655                   0.420557   
2                       47.451935                   0.315524   
3                       44.737083                   0.401709   
4                       45.334518                   0.390626   

   original_shape_SurfaceArea  original_shape_SurfaceVolumeRatio  \
0                 4482.023762                           0.637270   
1                 4490.310227                           0.581904   
2                 5412.437400                           0.815607   
3                 4914.650931                           0.595818   
4                 4041.249915                           0.685214   

   original_shape_VoxelVolume  original_firstorder_10Percentile  \
0                        7106                              56.0   
1                        7779                              56.0   
2                        6707                              34.0   
3                        8281                              59.0   
4                        5986                              60.0   

   original_firstorder_90Percentile  original_firstorder_Energy  \
0                              83.0                    35914043   
1                              82.0                    38292768   
2                              

In [112]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 303 entries, 0 to 304
Data columns (total 2018 columns):
 #     Column                                                         Non-Null Count  Dtype  
---    ------                                                         --------------  -----  
 0     diagnostics_Image-original_Mean                                303 non-null    float64
 1     diagnostics_Image-original_Maximum                             303 non-null    int64  
 2     diagnostics_Mask-original_VoxelNum                             303 non-null    int64  
 3     original_shape_Elongation                                      303 non-null    float64
 4     original_shape_Flatness                                        303 non-null    float64
 5     original_shape_LeastAxisLength                                 303 non-null    float64
 6     original_shape_MajorAxisLength                                 303 non-null    float64
 7     original_shape_Maximum2DDiameterColumn       

**Binary features?**

In [113]:
binary = [col for col, count in unique_dict.items() if count == 2]
for col in binary:
    print(col)
print("Total:", len(binary))

lbp-2D_firstorder_90Percentile
lbp-2D_firstorder_Median
Sex
Total: 3


In [114]:
float_df = df.select_dtypes(include='float')

# Calculating skewness and kurtosis
skewness = float_df.skew()
kurtosis = float_df.kurt()
skew = zip(skewness,df.columns)
skew = enumerate(sorted(skew,reverse=True,key = (lambda x:abs(x[0]))))
skew_ranking = map(lambda xyz : (xyz[1][1],xyz[0],xyz[1][0]) ,skew)
list(skew_ranking)

[('log-sigma-5-0-mm-3D_glszm_SizeZoneNonUniformity', 0, 14.882374524621843),
 ('logarithm_firstorder_Median', 1, 9.61531209314427),
 ('square_glszm_SizeZoneNonUniformity', 2, 9.116775688768419),
 ('logarithm_glrlm_RunVariance', 3, 8.873655513292007),
 ('wavelet-HLH_gldm_LargeDependenceLowGrayLevelEmphasis', 4, 8.56435260665547),
 ('wavelet-HLH_glcm_SumEntropy', 5, 8.556089502549357),
 ('wavelet-HLH_firstorder_Minimum', 6, 8.556085984888352),
 ('wavelet-HLH_glcm_DifferenceVariance', 7, 8.545649280427332),
 ('wavelet-HLH_glcm_Imc1', 8, 8.545649280427332),
 ('wavelet-HLH_gldm_SmallDependenceLowGrayLevelEmphasis',
  9,
  -8.530106870014292),
 ('wavelet-HLH_glrlm_LongRunLowGrayLevelEmphasis', 10, 8.488574793786825),
 ('wavelet-HLH_gldm_DependenceNonUniformityNormalized',
  11,
  -8.487854060225379),
 ('wavelet-HLH_glrlm_LowGrayLevelRunEmphasis', 12, -8.156382285595793),
 ('wavelet-HLH_gldm_DependenceEntropy', 13, 8.1368187522141),
 ('wavelet-HLH_gldm_SmallDependenceEmphasis', 14, 8.02214984

In [115]:
kurtosis = float_df.kurt()
kurt = zip(kurtosis,df.columns)
kurt = sorted(kurt,reverse=True,key = (lambda x:abs(x[0])))
kurt_ranking = map(lambda xyz : (xyz[1][1],xyz[0],xyz[1][0]) ,enumerate(kurt))
list(kurt_ranking)

[('log-sigma-5-0-mm-3D_glszm_SizeZoneNonUniformity', 0, 242.6337542165045),
 ('logarithm_firstorder_Median', 1, 115.167760142742),
 ('logarithm_glrlm_RunVariance', 2, 113.1560984227086),
 ('square_glszm_SizeZoneNonUniformity', 3, 93.73029980127536),
 ('wavelet-HLL_glrlm_ShortRunHighGrayLevelEmphasis', 4, 75.77255582019866),
 ('wavelet-HLH_gldm_LargeDependenceLowGrayLevelEmphasis', 5, 71.8720021239621),
 ('wavelet-HLH_glcm_SumEntropy', 6, 71.77935473060452),
 ('wavelet-HLH_firstorder_Minimum', 7, 71.7789351174761),
 ('wavelet-HLH_glcm_Imc1', 8, 71.66007686675754),
 ('wavelet-HLH_glcm_DifferenceVariance', 9, 71.6600768667575),
 ('wavelet-HLH_gldm_SmallDependenceLowGrayLevelEmphasis',
  10,
  71.48295193691075),
 ('wavelet-HLH_glrlm_LongRunLowGrayLevelEmphasis', 11, 71.0750823218485),
 ('wavelet-HLH_gldm_DependenceNonUniformityNormalized', 12, 71.00357639699256),
 ('logarithm_firstorder_Minimum', 13, 68.82225547010762),
 ('wavelet-HLH_gldm_DependenceEntropy', 14, 67.41958965644996),
 ('wa

### **Models**

Split data

In [145]:
X = df.drop('Transition', axis=1)
y = df['Transition']

float_X = X.select_dtypes(include='float')


normalized_float_X = MinMaxScaler().fit_transform(float_X)
chi2_scores, p_values = chi2(normalized_float_X, y)

chi2_results = pd.DataFrame({
     'Feature': float_X.columns,
     'Chi2 Score': chi2_scores,
     'p-Value': p_values
 })

chi2_results = chi2_results[chi2_results['p-Value'] < 0.05]
sorted_chi2_results = chi2_results.sort_values(by='Chi2 Score', ascending=False).reset_index(drop=True)
selected_features = sorted_chi2_results['Feature'].tolist()
X = X[selected_features]

In [148]:

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=2024)

X.head()
X.columns

Index(['lbp-3D-m1_firstorder_Median', 'lbp-2D_gldm_DependenceVariance',
       'lbp-3D-m2_gldm_DependenceVariance',
       'lbp-3D-m1_gldm_DependenceVariance',
       'lbp-2D_gldm_SmallDependenceHighGrayLevelEmphasis',
       'lbp-3D-m2_gldm_SmallDependenceLowGrayLevelEmphasis',
       'lbp-2D_gldm_SmallDependenceLowGrayLevelEmphasis',
       'lbp-2D_gldm_SmallDependenceEmphasis',
       'lbp-3D-m2_gldm_SmallDependenceEmphasis',
       'lbp-3D-m1_gldm_SmallDependenceEmphasis',
       'lbp-3D-m1_gldm_SmallDependenceLowGrayLevelEmphasis',
       'lbp-3D-m2_gldm_SmallDependenceHighGrayLevelEmphasis',
       'lbp-3D-m1_gldm_SmallDependenceHighGrayLevelEmphasis',
       'gradient_firstorder_Median',
       'lbp-3D-m1_glrlm_ShortRunLowGrayLevelEmphasis',
       'lbp-3D-m1_glrlm_ShortRunHighGrayLevelEmphasis',
       'lbp-2D_glrlm_ShortRunLowGrayLevelEmphasis',
       'lbp-3D-m1_glrlm_ShortRunEmphasis',
       'lbp-3D-m2_glrlm_ShortRunHighGrayLevelEmphasis',
       'lbp-3D-m2_glrlm_ShortRunEm

#### Decision Tree

In [61]:
dt_model = DecisionTreeClassifier(max_depth=2, random_state=2024)
dt_model.fit(X_train, y_train)

DecisionTreeClassifier(max_depth=2, random_state=2024)

In [62]:
dt_score = dt_model.score(X_test, y_test)
print("Accuracy: %.2f%%" % (dt_score * 100))

Accuracy: 44.26%
